In [1]:
%run "/Users/ananshar/Desktop/Work/Projects/DSC214-Soccer-Passing-Network-Analysis/features_test.ipynb"

Average Distance: 0.6066217110955285
Percentage of Through Balls: 0
Pass Completion Rate: 53.98936170212766
Average Passes Per Player: 26.857142857142858
Most Advanced Player: Bojan Krkíc Pérez
Number of Passes Received by the Most Advanced Player: 9
Average X Position (excluding goalkeepers): 0.520929307116105
Average Number of Unique Passing Links per Player: 7.642857142857143
Average Team VAEP Value: 0.01752521122894877
Average Pass Distance: 0.21809361230574542
Average Distance of the Back Four from Own Goal: 0.4208461911951512
Average Distance of the Front Three from Own Goal: 0.6890277777777779
Average Time Between Passes for Barcelona: 3.734752516453736


/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_goalkeepers["origin_pos_x"] = df.location.apply(lambda x: _statsbomb_to_point(x)[0])
/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/socceraction/vaep.py:37: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.0465' has dtype incompatible with float32, please explicitly cast to a compatible dtype first.
  prev_scores[corner_idx] = 0.046500
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/2725290664.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling back

Average Number of Passes Per Possession for Barcelona: 2.647887323943662
From Recovery Passes: 0.375
From Throw-in Passes: 0.3723404255319149
From Free Kick Passes: 0.09574468085106383
From Corner Passes: 0.015957446808510637
From Goal Kick Passes: 0.0851063829787234
From Interception Passes: 0.010638297872340425
From Kick Off Passes: 0.023936170212765957
Average Directness of Play: 0.12459884751773048
Betti 0: 1
Betti 1: 57


In [2]:
import pandas as pd
from pandas import json_normalize
from utils import read_json
import socceraction.vaep as vaep
import numpy as np
import pandas as pd
import json
import warnings
import os
import networkx as nx

In [3]:
datafolder = 'data/eventing'

matches = os.path.join(datafolder, "matches")
lineups = os.path.join(datafolder, "lineups")
events = os.path.join(datafolder, "events")

In [4]:
def get_file_paths(directory):
    season_paths = []

    for item in os.listdir(directory):
        file_path = os.path.join(directory, item)

        # Check if the item is a directory
        if os.path.isdir(file_path):
            # List all contents of the directory
            for content in os.listdir(file_path):
                content_path = os.path.join(file_path, content)

                if content.endswith(".json"):
                    season_paths.append(content_path)

    return season_paths

season_paths = get_file_paths(matches)
print(season_paths)

['data/eventing/matches/11/41.json', 'data/eventing/matches/11/40.json', 'data/eventing/matches/11/37.json', 'data/eventing/matches/11/21.json', 'data/eventing/matches/11/26.json', 'data/eventing/matches/11/27.json', 'data/eventing/matches/11/1.json', 'data/eventing/matches/11/2.json', 'data/eventing/matches/11/90.json', 'data/eventing/matches/11/24.json', 'data/eventing/matches/11/278.json', 'data/eventing/matches/11/25.json', 'data/eventing/matches/11/22.json', 'data/eventing/matches/11/38.json', 'data/eventing/matches/11/4.json', 'data/eventing/matches/11/42.json', 'data/eventing/matches/11/39.json', 'data/eventing/matches/11/23.json']


In [5]:
predictions_h5 = os.path.join("data/eventing", "predictions.h5")

spadl_h5 = os.path.join("data/eventing", "spadl-statsbomb.h5")

actiontypes = pd.read_hdf(spadl_h5, "actiontypes")
bodyparts = pd.read_hdf(spadl_h5, "bodyparts")
results = pd.read_hdf(spadl_h5, "results")
players = pd.read_hdf(spadl_h5, "players")
teams = pd.read_hdf(spadl_h5, "teams")

In [6]:
df_season = pd.DataFrame()

for season_path in season_paths:
    season = read_json(season_path)
    df_season = pd.concat([df_season, json_normalize(season, sep="_")])

df_season.shape

(868, 42)

In [7]:
def get_outcome(x):
    if x["home_score"] > x["away_score"]:
        return "team1_wins"
    elif x["home_score"] < x["away_score"]:
        return "team2_wins"
    else:
        return "draw"

df_season["outcome"] = df_season.apply(get_outcome, axis=1)


In [8]:
df_season.head()

match_id  match_date      kick_off  home_score  away_score match_status  \
0     69225  2008-12-13  22:00:00.000           2           0    available   
1     69212  2008-10-04  22:00:00.000           6           1    available   
2     69235  2008-11-01  20:00:00.000           1           4    available   
3     69232  2008-10-25  22:00:00.000           5           0    available   
4     69216  2009-03-07  20:00:00.000           2           0    available   

  match_status_360      last_updated         last_updated_360  match_week  \
0        scheduled  2020-07-29T05:00  2021-06-13T16:17:31.694          15   
1        scheduled  2020-07-29T05:00  2021-06-13T16:17:31.694           6   
2        scheduled  2020-07-29T05:00  2021-06-13T16:17:31.694           9   
3        scheduled  2020-07-29T05:00  2021-06-13T16:17:31.694           8   
4        scheduled  2020-07-29T05:00  2021-06-13T16:17:31.694          26   

   competition_competition_id competition_country_name  \
0                          11                    Spain   
1                          11                    Spain   
2                          11                    Spain   
3                          11                    Spain   
4                          11                    Spain   

  competition_competition_name  season_season_id season_season_name  \
0                      La Liga                41          2008/2009   
1                      La Liga                41          2008/2009   
2                      La Liga                41          2008/2009   
3                      La Liga                41          2008/2009   
4                      La Liga                41          2008/2009   

   home_team_home_team_id home_team_home_team_name home_team_home_team_gender  \
0                     217                Barcelona                       male   
1                     217                Barcelona                       male   
2                     223                   Málaga                       male   
3                     217                Barcelona                       male   
4                     217                Barcelona                       male   

  home_team_home_team_group  home_team_country_id home_team_country_name  \
0                      None                   214                  Spain   
1                      None                   214                  Spain   
2                      None                   214                  Spain   
3                      None                   214                  Spain   
4                      None                   214                  Spain   

                                  home_team_managers  away_team_away_team_id  \
0  [{'id': 36, 'name': 'Josep Guardiola i Sala', ...                     220   
1  [{'id': 36, 'name': 'Josep Guardiola i Sala', ...                     212   
2  [{'id': 4989, 'name': 'Antonio Tapia Flores', ...                     217   
3                                                NaN                     403   
4  [{'id': 36, 'name': 'Josep Guardiola i Sala', ...                     215   

  away_team_away_team_name away_team_away_team_gender  \
0              Real Madrid                       male   
1          Atlético Madrid                       male   
2                Barcelona                       male   
3                  Almería                       male   
4            Athletic Club                       male   

  away_team_away_team_group  away_team_country_id away_team_country_name  \
0                      None                   214                  Spain   
1                      None                   214                  Spain   
2                      None                   214                  Spain   
3                      None                   214                  Spain   
4                      None                   214                  Spain   

                                  away_team_managers metadata_data_ver

In [9]:
match_data = df_season[df_season["match_id"] == 69212]
# team_names = [
#     match_data["home_team_home_team_name"],
#     match_data["away_team_away_team_name"],
# ]
# team_names
list(match_data["home_team_home_team_name"])[0]

'Barcelona'

In [10]:
match_ids = [match["match_id"] for season_path in season_paths for match in read_json(season_path)]

In [11]:
# match_id = 68352
match_data = []

for match_id in match_ids:

    print(f"-----------Processing {match_id}.json-----------")

    actions = pd.read_hdf(spadl_h5, "actions/game_{0}".format(match_id))

    actions = (
    actions.merge(actiontypes, how="left")
    .merge(results, how="left")
    .merge(bodyparts, how="left")
    .merge(players, how="left")
    .merge(teams, how="left")
    )

    game_data = df_season[df_season["match_id"] == match_id]

    match_outcome = list(game_data['outcome'])[0]

    preds = pd.read_hdf(predictions_h5, "game_{0}".format(match_id))
    values = vaep.value(actions, preds.scores, preds.concedes)

    lineup = read_json(f"data/eventing/lineups/{match_id}.json")

    # Team 1 - Home Team, Team 2 - Away Team
    team_names = [
        list(game_data["home_team_home_team_name"])[0],
        list(game_data["away_team_away_team_name"])[0],
    ]

    # print(team_names)

    names_dict = {
        player["player_name"]: player["player_nickname"]
        for team in lineup
        for player in team["lineup"]
    }

    match_events = read_json(os.path.join(events, f"{match_id}.json"))
    df_events = json_normalize(match_events, sep="_").assign(match_id=match_id)

    match_row = {"match_id": match_id}

    for team in team_names:

        team_prefix = f"team{team_names.index(team) + 1}_"

        print(f"-----------Team: {team}-----------")

        df_passes = df_events[
            (df_events.type_name == "Pass")
            & (df_events.pass_outcome_name != "Injury Clearance")
            & (df_events.team_name == team)
            # & (df_events.minute < num_minutes)
        ].copy()

        goal = (1, 0.5)
        average_distance = calculate_average_distance_from_goal(df_passes, goal)
        print("Average Distance:", average_distance)

        pass_type_counts = count_pass_type(df_passes, dropna=False, normalize=True)

        recovery_passes = pass_type_counts.get("Recovery", 0)
        throw_in_passes = pass_type_counts.get("Throw-in", 0)
        free_kick_passes = pass_type_counts.get("Free Kick", 0)
        corner_passes = pass_type_counts.get("Corner", 0)
        goal_kick_passes = pass_type_counts.get("Goal Kick", 0)
        interception_passes = pass_type_counts.get("Interception", 0)
        kick_off_passes = pass_type_counts.get("Kick Off", 0)

        # Print values to verify
        print("Recovery Passes:", recovery_passes)
        print("Throw-in Passes:", throw_in_passes)
        print("Free Kick Passes:", free_kick_passes)
        print("Corner Passes:", corner_passes)
        print("Goal Kick Passes:", goal_kick_passes)
        print("Interception Passes:", interception_passes)
        print("Kick Off Passes:", kick_off_passes)

        through_ball_percentage = calculate_through_ball_percentage(
            df_passes, dropna=False
        )
        print("Percentage of Through Balls:", through_ball_percentage)

        pass_completion_rate = calculate_pass_completion_rate(df_passes)
        print("Pass Completion Rate:", pass_completion_rate)

        avg_passes_per_player = calculate_avg_passes_per_player(df_passes)
        print("Average Passes Per Player:", avg_passes_per_player)

        most_advanced_player, number_of_passes_received = (
            calculate_passes_to_most_advanced_player(df_passes)
        )
        print("Most Advanced Player:", most_advanced_player)
        print(
            "Number of Passes Received by the Most Advanced Player:",
            number_of_passes_received,
        )

        avg_x_position_non_gk = calculate_avg_x_position_excluding_goalkeepers(
            df_passes
        )
        print("Average X Position (excluding goalkeepers):", avg_x_position_non_gk)

        avg_links = average_unique_passing_links(df_passes)
        print("Average Number of Unique Passing Links per Player:", avg_links)

        def get_name_or_default(name):
            if not name or pd.isna(name):  # Checks if name is None or NaN
                return None
            # Safely gets the value from the dictionary or returns the name itself
            return (
                names_dict.get(name, name) if names_dict.get(name) is not None else name
            )

        # If available, use player's nickname instead of full name to optimize space in plot
        # df_new["pass_recipient_name"] = df_new.pass_recipient_name.apply(lambda x: None if not x else names_dict[x] if names_dict[x] else x)
        df_passes["pass_recipient_name"] = df_passes["pass_recipient_name"].apply(get_name_or_default)
        df_passes["player_name"] = df_passes.player_name.apply(
            lambda x: names_dict[x] if names_dict[x] else x
        )

        df_vaep = pd.concat([actions, preds, values], axis=1)
        # df_vaep["player_name"] = df_vaep.apply(lambda x: x["player_nickname"] if x["player_nickname"] else x["player_name"], axis=1)
        df_vaep["player_name"] = df_vaep.player_name.apply(
            lambda x: names_dict[x] if names_dict[x] else x
        )

        team_pass_value = calculate_team_pass_value(df_passes, df_vaep)
        print("Average Team VAEP Value:", team_pass_value)

        avg_pass_distance = calculate_avg_pass_distance(df_passes)
        print("Average Pass Distance:", average_pass_distance)

        avg_backline_distance = calculate_backline_distance(df_passes, player_position_no_gk)
        print("Average Distance of the Back Four from Own Goal:", avg_backline_distance)

        avg_front_three_distance = calculate_front_three_distance(df_passes, player_position_no_gk)
        print("Average Distance of the Front Three from Own Goal:", avg_front_three_distance)

        avg_time_between_passes = calculate_avg_time_between_passes(df_passes)
        print(f"Average Time Between Passes:", average_time_between_passes)

        avg_passes_per_possession = calculate_global_avg_passes_per_possession(df_passes)
        print(f"Average Number of Passes Per Possession:",average_passes_per_possession)

        play_pattern_count = calculate_play_pattern_count(df_passes, normalize=True)

        from_recovery_passes = play_pattern_count.get("Regular Play", 0)
        from_throw_in_passes = play_pattern_count.get("From Throw In", 0)
        from_free_kick_passes = play_pattern_count.get("From Free Kick", 0)
        from_corner_passes = play_pattern_count.get("From Corner", 0)
        from_goal_kick_passes = play_pattern_count.get("From Goal Kick", 0)
        from_interception_passes = play_pattern_count.get("From Keeper", 0)
        from_kick_off_passes = play_pattern_count.get("From Kick Off", 0)

        print("From Recovery Passes:", from_recovery_passes)
        print("From Throw-in Passes:", from_throw_in_passes)
        print("From Free Kick Passes:", from_free_kick_passes)
        print("From Corner Passes:", from_corner_passes)
        print("From Goal Kick Passes:", from_goal_kick_passes)
        print("From Interception Passes:", from_interception_passes)
        print("From Kick Off Passes:", from_kick_off_passes)

        average_directness = calculate_directness_of_play(df_passes)
        print("Average Directness of Play:", average_directness)

        df_passes["pair_key"] = df_passes.apply(lambda x: (
        "_".join(sorted([x["player_name"], x["pass_recipient_name"]]))
        if x["player_name"] is not None and x["pass_recipient_name"] is not None
        else None), axis=1)

        pair_pass_count = df_passes.groupby("pair_key").size().to_frame("num_passes")

        # pair_pass_count["pair_key"] = pair_pass_count.index
        # pair_pass_count = pair_pass_count.reset_index(drop=True)
        pair_pass_count = pair_pass_count.reset_index()

        # pair_pass_count = pd.DataFrame(pair_pass_count)
        pair_pass_count.set_index("pair_key", inplace=True)

        # Create a graph from the DataFrame
        G = nx.Graph()

        # Add edges to the graph
        for pair_key, num_passes in pair_pass_count["num_passes"].items():
            player1, player2 = pair_key.split("_")
            G.add_edge(player1, player2, weight=num_passes)

        # Calculate Betti numbers for the graph
        betti_0, betti_1 = calculate_betti_numbers(G)
        print(f"Betti 0: {betti_0}")
        print(f"Betti 1: {betti_1}")

        match_row.update(
            {
                f"{team_prefix}name": team,
                f"{team_prefix}average_distance": average_distance,
                f"{team_prefix}recovery_passes": recovery_passes,
                f"{team_prefix}throw_in_passes": throw_in_passes,
                f"{team_prefix}free_kick_passes": free_kick_passes,
                f"{team_prefix}corner_passes": corner_passes,
                f"{team_prefix}goal_kick_passes": goal_kick_passes,
                f"{team_prefix}interception_passes": interception_passes,
                f"{team_prefix}kick_off_passes": kick_off_passes,
                f"{team_prefix}through_ball_percentage": through_ball_percentage,
                f"{team_prefix}pass_completion_rate": pass_completion_rate,
                f"{team_prefix}avg_passes_per_player": avg_passes_per_player,
                f"{team_prefix}most_advanced_player": most_advanced_player,
                f"{team_prefix}number_of_passes_received": number_of_passes_received,
                f"{team_prefix}avg_x_position_non_gk": avg_x_position_non_gk,
                f"{team_prefix}avg_links": avg_links,
                f"{team_prefix}avg_pass_distance": avg_pass_distance,
                f"{team_prefix}avg_backline_distance": avg_backline_distance,
                f"{team_prefix}avg_front_three_distance": avg_front_three_distance,
                f"{team_prefix}avg_time_between_passes": avg_time_between_passes,
                f"{team_prefix}avg_x_position_non_gk": avg_x_position_non_gk,
                f"{team_prefix}avg_passes_per_possession": avg_passes_per_possession,
                f"{team_prefix}betti_0": betti_0,
                f"{team_prefix}betti_1": betti_1,
            }
        )

    match_row.update(
        {
            "match_outcome": match_outcome,
        }
    )

    match_data.append(match_row)

-----------Processing 69225.json-----------
-----------Team: Barcelona-----------
Average Distance: 0.5487638102935728
Recovery Passes: 0.09931506849315068
Throw-in Passes: 0.0410958904109589
Free Kick Passes: 0.032534246575342464
Corner Passes: 0.018835616438356163
Goal Kick Passes: 0.008561643835616438
Interception Passes: 0.003424657534246575
Kick Off Passes: 0.0017123287671232876
Percentage of Through Balls: 2.5684931506849313
Pass Completion Rate: 81.84931506849315
Average Passes Per Player: 44.92307692307692
Most Advanced Player: Thierry Henry
Number of Passes Received by the Most Advanced Player: 47
Average X Position (excluding goalkeepers): 0.5534174041297936
Average Number of Unique Passing Links per Player: 8.307692307692308
Average Team VAEP Value: 0.015936307649282402
Average Pass Distance: 0.21809361230574542
Average Distance of the Back Four from Own Goal: 0.4208461911951512
Average Distance of the Front Three from Own Goal: 0.6890277777777779
Average Time Between Passes

/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/socceraction/vaep.py:33: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.792453' has dtype incompatible with float32, please explicitly cast to a compatible dtype first.
  prev_scores[penalty_idx] = 0.792453
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_goalkeepers["origin_pos_x"] = df.location.apply(lambda x: _statsbomb_to_point(x)[0])
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/2725290664.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling b

-----------Team: Barcelona-----------
Average Distance: 0.5713022975150953
Recovery Passes: 0.045531197301854974
Throw-in Passes: 0.03035413153456998
Free Kick Passes: 0.02866779089376054
Corner Passes: 0.008431703204047217
Goal Kick Passes: 0.003372681281618887
Interception Passes: 0.008431703204047217
Kick Off Passes: 0.003372681281618887
Percentage of Through Balls: 0.5059021922428331
Pass Completion Rate: 85.83473861720068
Average Passes Per Player: 42.357142857142854
Most Advanced Player: Thierry Henry
Number of Passes Received by the Most Advanced Player: 19
Average X Position (excluding goalkeepers): 0.5324712643678161
Average Number of Unique Passing Links per Player: 9.071428571428571
Average Team VAEP Value: 0.009647751774948529
Average Pass Distance: 0.21809361230574542
Average Distance of the Back Four from Own Goal: 0.4208461911951512
Average Distance of the Front Three from Own Goal: 0.6890277777777779
Average Time Between Passes: 3.734752516453736
Average Number of Passe

/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_goalkeepers["origin_pos_x"] = df.location.apply(lambda x: _statsbomb_to_point(x)[0])
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/2725290664.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  team_passes["timestamp"] = pd.to_datetime(team_passes["timestamp"], errors="coerce")
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .lo

-----------Team: Barcelona-----------
Average Distance: 0.5337476123687772
Recovery Passes: 0.043209876543209874
Throw-in Passes: 0.029320987654320986
Free Kick Passes: 0.024691358024691357
Corner Passes: 0.009259259259259259
Goal Kick Passes: 0.006172839506172839
Interception Passes: 0.0030864197530864196
Kick Off Passes: 0.0015432098765432098
Percentage of Through Balls: 0.4629629629629629
Pass Completion Rate: 88.73456790123457
Average Passes Per Player: 46.285714285714285
Most Advanced Player: Samuel Eto''o Fils
Number of Passes Received by the Most Advanced Player: 47
Average X Position (excluding goalkeepers): 0.5724265091863517
Average Number of Unique Passing Links per Player: 9.357142857142858
Average Team VAEP Value: 0.019080056860598327
Average Pass Distance: 0.21809361230574542
Average Distance of the Back Four from Own Goal: 0.4208461911951512
Average Distance of the Front Three from Own Goal: 0.6890277777777779
Average Time Between Passes: 3.734752516453736
Average Number

...

/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/2725290664.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  team_passes["timestamp"] = pd.to_datetime(team_passes["timestamp"], errors="coerce")
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_goalkeepers["origin_pos_x"] = df.location.apply(lambda x: _statsbomb_to_point(x)[0])
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/2725290664.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateuti

Average Time Between Passes: 3.734752516453736
Average Number of Passes Per Possession: 2.647887323943662
From Recovery Passes: 0.24651162790697675
From Throw-in Passes: 0.20930232558139536
From Free Kick Passes: 0.15813953488372093
From Corner Passes: 0.05581395348837209
From Goal Kick Passes: 0.07441860465116279
From Interception Passes: 0.004651162790697674
From Kick Off Passes: 0.20930232558139536
Average Directness of Play: 0.11105426356589146
Betti 0: 1
Betti 1: 55
-----------Processing 70224.json-----------
-----------Team: Rayo Vallecano-----------
Average Distance: 0.640718162657869
Recovery Passes: 0.11570247933884298
Throw-in Passes: 0.08264462809917356
Free Kick Passes: 0.03305785123966942
Corner Passes: 0.028925619834710745
Goal Kick Passes: 0.028925619834710745
Interception Passes: 0
Kick Off Passes: 0.03305785123966942
Percentage of Through Balls: 0.0
Pass Completion Rate: 61.57024793388429
Average Passes Per Player: 17.285714285714285
Most Advanced Player: Alhassane Ban

/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/socceraction/vaep.py:33: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.792453' has dtype incompatible with float32, please explicitly cast to a compatible dtype first.
  prev_scores[penalty_idx] = 0.792453
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_goalkeepers["origin_pos_x"] = df.location.apply(lambda x: _statsbomb_to_point(x)[0])
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/2725290664.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling b

-----------Team: Levante UD-----------
Average Distance: 0.6561326217418993
Recovery Passes: 0.11036789297658862
Throw-in Passes: 0.0903010033444816
Free Kick Passes: 0.023411371237458192
Corner Passes: 0.0033444816053511705
Goal Kick Passes: 0.033444816053511704
Interception Passes: 0.0033444816053511705
Kick Off Passes: 0.010033444816053512
Percentage of Through Balls: 3.3444816053511706
Pass Completion Rate: 68.89632107023411
Average Passes Per Player: 23.0
Most Advanced Player: Rubén Suárez Estrada
Number of Passes Received by the Most Advanced Player: 5
Average X Position (excluding goalkeepers): 0.4918942307692308
Average Number of Unique Passing Links per Player: 7.923076923076923
Average Team VAEP Value: 0.00803310282090489
Average Pass Distance: 0.21809361230574542
Average Distance of the Back Four from Own Goal: 0.4208461911951512
Average Distance of the Front Three from Own Goal: 0.6890277777777779
Average Time Between Passes: 3.734752516453736
Average Number of Passes Per P

/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_goalkeepers["origin_pos_x"] = df.location.apply(lambda x: _statsbomb_to_point(x)[0])
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/2725290664.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  team_passes["timestamp"] = pd.to_datetime(team_passes["timestamp"], errors="coerce")
/var/folders/gl/s_1pz2z130g9ct6hvptjf5fh0000gn/T/ipykernel_3093/1849874024.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .lo

In [19]:
df_matches = pd.DataFrame(match_data)
df_matches.shape

(868, 48)

In [20]:
df_matches.head()

match_id team1_name  team1_average_distance  team1_recovery_passes  \
0     69225  Barcelona                0.548764               0.099315   
1     69212  Barcelona                0.571302               0.045531   
2     69235     Málaga                0.627899               0.221477   
3     69232  Barcelona                0.533748               0.043210   
4     69216  Barcelona                0.595450               0.071082   

   team1_throw_in_passes  team1_free_kick_passes  team1_corner_passes  \
0               0.041096                0.032534             0.018836   
1               0.030354                0.028668             0.008432   
2               0.107383                0.080537             0.003356   
3               0.029321                0.024691             0.009259   
4               0.029079                0.048465             0.008078   

   team1_goal_kick_passes  team1_interception_passes  team1_kick_off_passes  \
0                0.008562                   0.003425               0.001712   
1                0.003373                   0.008432               0.003373   
2                0.033557                   0.013423               0.016779   
3                0.006173                   0.003086               0.001543   
4                0.009693                   0.001616               0.001616   

   team1_through_ball_percentage  team1_pass_completion_rate  \
0                       2.568493                   81.849315   
1                       0.505902                   85.834739   
2                       0.000000                   47.651007   
3                       0.462963                   88.734568   
4                       0.646204                   84.168013   

   team1_avg_passes_per_player    team1_most_advanced_player  \
0                    44.923077                 Thierry Henry   
1                    42.357143                 Thierry Henry   
2                    21.285714  Sérgio Paulo Barbosa Valente   
3                    46.285714            Samuel Eto''o Fils   
4                    47.615385                 Thierry Henry   

   team1_number_of_passes_received  team1_avg_x_position_non_gk  \
0                               47                     0.553417   
1                               19                     0.532471   
2                               35                     0.510701   
3                               47                     0.572427   
4                               42                     0.516839   

   team1_avg_links  team1_avg_pass_distance  team1_avg_backline_distance  \
0         8.307692                 0.224801                     0.420846   
1         9.071429                 0.214602                     0.420846   
2         6.071429                 0.256834                     0.420846   
3         9.357143                 0.210027                     0.420846   
4         8.307692                 0.246556                     0.420846   

   team1_avg_front_three_distance  team1_avg_time_between_passes  \
0                        0.689028                       3.850523   
1                        0.689028                       3.234646   
2                        0.689028                       4.852530   
3                        0.689028                       3.434116   
4                        0.689028                       3.700968   

   team1_avg_passes_per_possession  team1_betti_0  team1_betti_1  \
0                         4.598425              1             50   
1                         5.342342              1             62   
2                         2.257576              1             46   
3                         6.352941              1             64   
4                         5.429825              1             49   

        team2_name  team2_average_distance  team2_recovery_passes  \
0      Real Madrid                0.649797               0.167742   
1  Atlético Madrid                0.635492               0.06588

In [21]:
df_matches['match_outcome'].value_counts()

match_outcome
team1_wins    420
team2_wins    274
draw          174
Name: count, dtype: int64

In [22]:
df_matches.to_csv("laliga_matches.csv", index=False)

In [23]:
del df_matches

In [24]:
df_matches = pd.read_csv('laliga_matches.csv', )
df_matches.head()

match_id team1_name  team1_average_distance  team1_recovery_passes  \
0     69225  Barcelona                0.548764               0.099315   
1     69212  Barcelona                0.571302               0.045531   
2     69235     Málaga                0.627899               0.221477   
3     69232  Barcelona                0.533748               0.043210   
4     69216  Barcelona                0.595450               0.071082   

   team1_throw_in_passes  team1_free_kick_passes  team1_corner_passes  \
0               0.041096                0.032534             0.018836   
1               0.030354                0.028668             0.008432   
2               0.107383                0.080537             0.003356   
3               0.029321                0.024691             0.009259   
4               0.029079                0.048465             0.008078   

   team1_goal_kick_passes  team1_interception_passes  team1_kick_off_passes  \
0                0.008562                   0.003425               0.001712   
1                0.003373                   0.008432               0.003373   
2                0.033557                   0.013423               0.016779   
3                0.006173                   0.003086               0.001543   
4                0.009693                   0.001616               0.001616   

   team1_through_ball_percentage  team1_pass_completion_rate  \
0                       2.568493                   81.849315   
1                       0.505902                   85.834739   
2                       0.000000                   47.651007   
3                       0.462963                   88.734568   
4                       0.646204                   84.168013   

   team1_avg_passes_per_player    team1_most_advanced_player  \
0                    44.923077                 Thierry Henry   
1                    42.357143                 Thierry Henry   
2                    21.285714  Sérgio Paulo Barbosa Valente   
3                    46.285714            Samuel Eto''o Fils   
4                    47.615385                 Thierry Henry   

   team1_number_of_passes_received  team1_avg_x_position_non_gk  \
0                               47                     0.553417   
1                               19                     0.532471   
2                               35                     0.510701   
3                               47                     0.572427   
4                               42                     0.516839   

   team1_avg_links  team1_avg_pass_distance  team1_avg_backline_distance  \
0         8.307692                 0.224801                     0.420846   
1         9.071429                 0.214602                     0.420846   
2         6.071429                 0.256834                     0.420846   
3         9.357143                 0.210027                     0.420846   
4         8.307692                 0.246556                     0.420846   

   team1_avg_front_three_distance  team1_avg_time_between_passes  \
0                        0.689028                       3.850523   
1                        0.689028                       3.234646   
2                        0.689028                       4.852530   
3                        0.689028                       3.434116   
4                        0.689028                       3.700968   

   team1_avg_passes_per_possession  team1_betti_0  team1_betti_1  \
0                         4.598425              1             50   
1                         5.342342              1             62   
2                         2.257576              1             46   
3                         6.352941              1             64   
4                         5.429825              1             49   

        team2_name  team2_average_distance  team2_recovery_passes  \
0      Real Madrid                0.649797               0.167742   
1  Atlético Madrid                0.635492               0.06588

In [26]:
df_matches.columns

Index(['match_id', 'team1_name', 'team1_average_distance',
       'team1_recovery_passes', 'team1_throw_in_passes',
       'team1_free_kick_passes', 'team1_corner_passes',
       'team1_goal_kick_passes', 'team1_interception_passes',
       'team1_kick_off_passes', 'team1_through_ball_percentage',
       'team1_pass_completion_rate', 'team1_avg_passes_per_player',
       'team1_most_advanced_player', 'team1_number_of_passes_received',
       'team1_avg_x_position_non_gk', 'team1_avg_links',
       'team1_avg_pass_distance', 'team1_avg_backline_distance',
       'team1_avg_front_three_distance', 'team1_avg_time_between_passes',
       'team1_avg_passes_per_possession', 'team1_betti_0', 'team1_betti_1',
       'team2_name', 'team2_average_distance', 'team2_recovery_passes',
       'team2_throw_in_passes', 'team2_free_kick_passes',
       'team2_corner_passes', 'team2_goal_kick_passes',
       'team2_interception_passes', 'team2_kick_off_passes',
       'team2_through_ball_percentage', 't

In [29]:
df_matches.shape

(868, 48)

In [31]:
drop_columns = [
    "match_outcome",
    "match_id",
    "team1_name",
    "team2_name",
    "team1_most_advanced_player",
    "team2_most_advanced_player",
]

y = np.array(df_matches.match_outcome)
X = df_matches.drop(drop_columns, axis=1)
print(X.shape, y.shape)

(868, 42) (868,)


In [32]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)

# Standardize the features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Initialize the classifier
clf = RandomForestClassifier(n_estimators=100, random_state=42)

# Train the classifier
clf.fit(X_train, y_train)

# Make predictions on the test set
y_pred = clf.predict(X_test)

# Evaluate the model
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy: {accuracy:.2f}")

# Classification report
print("Classification Report:")
print(classification_report(y_test, y_pred))

# Confusion matrix
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))

Accuracy: 0.83
Classification Report:
              precision    recall  f1-score   support

        draw       0.90      0.26      0.41        34
  team1_wins       0.83      1.00      0.91        87
  team2_wins       0.81      0.91      0.86        53

    accuracy                           0.83       174
   macro avg       0.85      0.72      0.72       174
weighted avg       0.84      0.83      0.79       174

Confusion Matrix:
[[ 9 14 11]
 [ 0 87  0]
 [ 1  4 48]]


In [33]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
import xgboost as xgb

# Load your dataset

X = df_matches.drop(drop_columns, axis=1)  # Features
y = df_matches["match_outcome"]  # Target variable

label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(
    X, y_encoded, test_size=0.2, random_state=42
)

# Standardize the features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Define models with default parameters
models = {
    "Logistic Regression": LogisticRegression(),
    "Random Forest": RandomForestClassifier(),
    "Support Vector Machine": SVC(),
    "XGBoost": xgb.XGBClassifier(),
}

# Perform cross-validation and evaluation
results = {}
for name, model in models.items():
    # Cross-validation
    cv_scores = cross_val_score(model, X_train, y_train, cv=5, scoring="accuracy")
    results[name] = {
        "cv_mean_accuracy": np.mean(cv_scores),
        "cv_std_accuracy": np.std(cv_scores),
    }
    # Train the model on the entire training set
    model.fit(X_train, y_train)
    y_train_pred = model.predict(X_train)
    results[name]["train_accuracy"] = accuracy_score(y_train, y_train_pred)
    # Evaluate the model on the test set
    y_pred = model.predict(X_test)
    results[name]["test_accuracy"] = accuracy_score(y_test, y_pred)
    results[name]["classification_report"] = classification_report(y_test, y_pred)
    results[name]["confusion_matrix"] = confusion_matrix(y_test, y_pred)

# Print results
for name, result in results.items():
    print(f"\n{name} Results:")
    print(f"Training Accuracy: {result['train_accuracy']:.4f}")
    print(f"Cross-Validation Mean Accuracy: {result['cv_mean_accuracy']:.4f}")
    print(f"Cross-Validation Std Accuracy: {result['cv_std_accuracy']:.4f}")
    print(f"Test Accuracy: {result['test_accuracy']:.4f}")
    print("Classification Report:")
    print(result["classification_report"])
    print("Confusion Matrix:")
    print(result["confusion_matrix"])


Logistic Regression Results:
Training Accuracy: 0.9150
Cross-Validation Mean Accuracy: 0.8387
Cross-Validation Std Accuracy: 0.0504
Test Accuracy: 0.8563
Classification Report:
              precision    recall  f1-score   support

           0       0.65      0.59      0.62        34
           1       0.92      0.97      0.94        87
           2       0.87      0.85      0.86        53

    accuracy                           0.86       174
   macro avg       0.81      0.80      0.81       174
weighted avg       0.85      0.86      0.85       174

Confusion Matrix:
[[20  7  7]
 [ 3 84  0]
 [ 8  0 45]]

Random Forest Results:
Training Accuracy: 1.0000
Cross-Validation Mean Accuracy: 0.7810
Cross-Validation Std Accuracy: 0.0276
Test Accuracy: 0.8218
Classification Report:
              precision    recall  f1-score   support

           0       0.71      0.29      0.42        34
           1       0.84      0.98      0.90        87
           2       0.81      0.91      0.86        

In [34]:
# Hyperparameter Tuning

models = {
    "Logistic Regression": LogisticRegression(),
    "XGBoost": xgb.XGBClassifier(),
}

In [35]:
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix


X = df_matches.drop(drop_columns, axis=1)  # Features
y = df_matches["match_outcome"]  # Target variable

label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(
    X, y_encoded, test_size=0.2, random_state=42
)

# Standardize the features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Define models with default parameters
models = {
    "Logistic Regression": LogisticRegression(),
    "XGBoost": xgb.XGBClassifier(),
}

# Define hyperparameter grids for tuning
param_grids = {
    "Logistic Regression": {
        "penalty": ["l1", "l2"],
        "C": [3, 5, 7],
        "solver": ["liblinear"],
    },
    "XGBoost": {
        "n_estimators": [100, 200],
        "max_depth": [3, 6, 9],
        "learning_rate": [0.01, 0.05],
        "subsample": [0.5, 0.7, 0.9],
    },
}

# Perform cross-validation, hyperparameter tuning, and evaluation
results = {}
for name, model in models.items():
    if name in param_grids:
        # Perform GridSearchCV for hyperparameter tuning
        grid_search = GridSearchCV(
            model, param_grids[name], cv=5, scoring="accuracy", n_jobs=-1
        )
        grid_search.fit(X_train, y_train)
        best_model = grid_search.best_estimator_
        results[name] = {
            "best_params": grid_search.best_params_,
            "cv_mean_accuracy": grid_search.best_score_,
            "cv_std_accuracy": np.std(grid_search.cv_results_["mean_test_score"]),
        }
    else:
        # Perform cross-validation with default parameters
        cv_scores = cross_val_score(model, X_train, y_train, cv=5, scoring="accuracy")
        results[name] = {
            "cv_mean_accuracy": np.mean(cv_scores),
            "cv_std_accuracy": np.std(cv_scores),
        }
        best_model = model
        best_model.fit(X_train, y_train)

    # Train the model on the entire training set
    best_model.fit(X_train, y_train)
    y_train_pred = best_model.predict(X_train)
    results[name]["train_accuracy"] = accuracy_score(y_train, y_train_pred)

    # Evaluate the model on the test set
    y_pred = best_model.predict(X_test)
    results[name]["test_accuracy"] = accuracy_score(y_test, y_pred)
    results[name]["classification_report"] = classification_report(y_test, y_pred)
    results[name]["confusion_matrix"] = confusion_matrix(y_test, y_pred)

# Print results
for name, result in results.items():
    print(f"\n{name} Results:")
    if "best_params" in result:
        print(f"Best Parameters: {result['best_params']}")
    print(f"Training Accuracy: {result['train_accuracy']:.4f}")
    print(f"Cross-Validation Mean Accuracy: {result['cv_mean_accuracy']:.4f}")
    print(f"Cross-Validation Std Accuracy: {result['cv_std_accuracy']:.4f}")
    print(f"Test Accuracy: {result['test_accuracy']:.4f}")
    print("Classification Report:")
    print(result["classification_report"])
    print("Confusion Matrix:")
    print(result["confusion_matrix"])


Logistic Regression Results:
Best Parameters: {'C': 7, 'penalty': 'l1', 'solver': 'liblinear'}
Training Accuracy: 0.9207
Cross-Validation Mean Accuracy: 0.8733
Cross-Validation Std Accuracy: 0.0156
Test Accuracy: 0.8621
Classification Report:
              precision    recall  f1-score   support

           0       0.71      0.50      0.59        34
           1       0.91      0.98      0.94        87
           2       0.84      0.91      0.87        53

    accuracy                           0.86       174
   macro avg       0.82      0.79      0.80       174
weighted avg       0.85      0.86      0.85       174

Confusion Matrix:
[[17  8  9]
 [ 2 85  0]
 [ 5  0 48]]

XGBoost Results:
Best Parameters: {'learning_rate': 0.05, 'max_depth': 3, 'n_estimators': 200, 'subsample': 0.7}
Training Accuracy: 0.9986
Cross-Validation Mean Accuracy: 0.8545
Cross-Validation Std Accuracy: 0.0197
Test Accuracy: 0.8908
Classification Report:
              precision    recall  f1-score   support

   

In [36]:
# Define Logistic Regression with L1 regularization
logistic_model = LogisticRegression(C=7, penalty="l1", solver="liblinear")
logistic_model.fit(X_train, y_train)

y_pred_train = logistic_model.predict(X_train)
y_pred_test = logistic_model.predict(X_test)
print(f"Train Accuracy: {accuracy_score(y_train, y_pred_train)}")
print(f"Test Accuracy: {accuracy_score(y_test, y_pred_test)}")

Train Accuracy: 0.920749279538905
Test Accuracy: 0.8620689655172413


In [37]:
X_train.shape

(694, 42)

In [38]:
# Retrain Logistic Regression using only the important features identified by L1 regularization
important_features = np.where(logistic_model.coef_ != 0)  # Indices of important features


class_indices, feature_indices = important_features
important_features

(array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]),
 array([ 0,  1,  2,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 17, 18, 20,
        21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 38, 39,
        41,  0,  1,  2,  3,  4,  5,  6,  7,  9, 10, 11, 13, 14, 17, 18, 20,
        22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 38, 39, 41,
         1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 17, 18, 20,
        21, 22, 23, 24, 25, 26, 28, 29, 30, 31, 32, 33, 34, 35, 38, 39, 41]))

In [39]:
unique_classes = np.unique(class_indices)
# common_features = set(feature_indices[class_indices == unique_classes[0]])

common_features = set(range(0,X_train.shape[1]))

for cls in unique_classes:
    common_features &= set(feature_indices[class_indices == cls])

common_features = sorted(list(common_features))
print("Common features across all classes:", common_features)

Common features across all classes: [1, 2, 4, 5, 6, 7, 9, 10, 11, 13, 14, 17, 18, 20, 22, 23, 24, 25, 26, 28, 29, 30, 31, 32, 33, 34, 35, 38, 39, 41]


In [40]:
unimportant_features = set(range(0, X_train.shape[1])) - set(common_features)
X.iloc[:, list(unimportant_features)]

team1_average_distance  team1_free_kick_passes  \
0                  0.548764                0.032534   
1                  0.571302                0.028668   
2                  0.627899                0.080537   
3                  0.533748                0.024691   
4                  0.595450                0.048465   
..                      ...                     ...   
863                0.661150                0.042493   
864                0.586429                0.016873   
865                0.640718                0.033058   
866                0.656133                0.023411   
867                0.555124                0.023179   

     team2_avg_backline_distance  team2_avg_front_three_distance  \
0                       0.420846                        0.689028   
1                       0.420846                        0.689028   
2                       0.420846                        0.689028   
3                       0.420846                        0.689028   
4                       0.420846                        0.689028   
..                           ...                             ...   
863                     0.420846                        0.689028   
864                     0.420846                        0.689028   
865                     0.420846                        0.689028   
866                     0.420846                        0.689028   
867                     0.420846                        0.689028   

     team1_through_ball_percentage  team2_betti_0  \
0                         2.568493              1   
1                         0.505902              1   
2                         0.000000              1   
3                         0.462963              1   
4                         0.646204              1   
..                             ...            ...   
863                       2.549575              1   
864                       1.124859              1   
865                       0.000000              1   
866                       3.344482              1   
867                       2.152318              1   

     team1_avg_x_position_non_gk  team1_avg_backline_distance  \
0                       0.553417                     0.420846   
1                       0.532471                     0.420846   
2                       0.510701                     0.420846   
3                       0.572427                     0.420846   
4                       0.516839                     0.420846   
..                           ...                          ...   
863                     0.460392                     0.420846   
864                     0.519562                     0.420846   
865                     0.494803                     0.420846   
866                     0.491894                     0.420846   
867                     0.549927                     0.420846   

     team1_avg_front_three_distance  team1_betti_0  team2_average_distance  \
0                          0.689028              1                0.649797   
1                          0.689028              1                0.635492   
2                          0.689028              1                0.606622   
3                          0.689028              1                0.629449   
4                          0.689028              1                0.648760   
..                              ...            ...                     ...   
863                        0.689028              1                0.579127   
864                        0.689028              1                0.612072   
865                        0.689028              1                0.582086   
866                        0.689028              1                0.499110   
867                        0.689028              1                0.696127   

     team2_interception_passes  
0                     0.019355  
1                     0.014118  
2                     0.015957  
3                     0.009146  
4      

In [42]:
X_train, X_test, y_train, y_test = train_test_split(
    X.iloc[:, common_features], y_encoded, test_size=0.2, random_state=42
)

# Define Logistic Regression with L1 regularization
logistic_model = LogisticRegression(C=7, penalty='l1', solver="liblinear")
logistic_model.fit(X_train, y_train)

y_pred_train = logistic_model.predict(X_train)
y_pred_test = logistic_model.predict(X_test)
print(f"Train Accuracy: {accuracy_score(y_train, y_pred_train)}")
print(f"Test Accuracy: {accuracy_score(y_test, y_pred_test)}")

Train Accuracy: 0.8097982708933718
Test Accuracy: 0.8045977011494253


In [45]:
from sklearn.feature_selection import SequentialFeatureSelector

X_train, X_test, y_train, y_test = train_test_split(
    X, y_encoded, test_size=0.2, random_state=42
)

logistic_model = LogisticRegression(C=7, penalty="l1", solver="liblinear")

# Perform forward selection
sfs = SequentialFeatureSelector(
    logistic_model,
    n_features_to_select="auto",
    direction="forward",
    scoring="accuracy",
    cv=5,
)
sfs.fit(X_train, y_train)

selected_features = sfs.get_support(indices=True)
print(f"Selected Features: {selected_features}")

/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/sklearn/svm/_base.py:1237: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/sklearn/svm/_base.py:1237: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/sklearn/svm/_base.py:1237: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/sklearn/svm/_base.py:1237: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/Users/ananshar/anaconda3/envs/soccer_analysis/lib/python3.10/site-packages/sklearn/svm/_base.py:1237: ConvergenceWarning: Liblinear failed to converge, increase the number of iter

Selected Features: [ 0  2  3  4  5  6  7  9 10 14 15 16 19 21 24 25 26 28 29 32 34]


In [46]:
# Train the model using the selected features
logistic_model.fit(X_train.iloc[:, selected_features], y_train)

y_pred_train = logistic_model.predict(X_train.iloc[:, selected_features])
y_pred_test = logistic_model.predict(X_test.iloc[:, selected_features])

train_accuracy = accuracy_score(y_train, y_pred_train)
test_accuracy = accuracy_score(y_test, y_pred_test)

print("\nPerformance Metrics Using Selected Features:")
print(f"Training Accuracy: {train_accuracy:.4f}")
print(f"Test Accuracy: {test_accuracy:.4f}")
print("Classification Report:")
print(classification_report(y_test, y_pred_test))
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred_test))


Performance Metrics Using Selected Features:
Training Accuracy: 0.8098
Test Accuracy: 0.7759
Classification Report:
              precision    recall  f1-score   support

           0       0.50      0.03      0.06        34
           1       0.77      0.99      0.87        87
           2       0.79      0.91      0.84        53

    accuracy                           0.78       174
   macro avg       0.69      0.64      0.59       174
weighted avg       0.72      0.78      0.70       174

Confusion Matrix:
[[ 1 21 12]
 [ 0 86  1]
 [ 1  4 48]]


In [ ]:
%pwd